In [33]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.model_selection import TimeSeriesSplit
from sklearn.linear_model import LinearRegression
from sklearn.metrics import r2_score, mean_squared_error
from lightgbm import LGBMRegressor
from xgboost import XGBRegressor

import re

# 0) Display sanity
pd.set_option("display.width", 160)
pd.set_option("display.max_columns", 120)
pd.set_option("display.max_rows", 120)

# 1) Load Data
df = pd.read_csv('kaggle/input/hull-tactical-market-prediction/train.csv')

In [34]:
non_feature_cols = ['market_forward_excess_returns', 'risk_free_rate', 'forward_returns', 'date_id']
feature_cols = [col for col in df.columns if col not in non_feature_cols]

SENTINAL_VALUE = -9999

flag_cols = []

for col in feature_cols:
    if df[col].isnull().any():
        flag_col_name = f'{col}_is_missing'
        flag_cols.append(flag_col_name)
        df[flag_col_name] = df[col].isnull().astype(int)

df[feature_cols] = df[feature_cols].fillna(SENTINAL_VALUE)

nan_count_features = df[feature_cols].isnull().sum().sum()
print(f"Total NaNs remaining in original features: {nan_count_features}")

Total NaNs remaining in original features: 0


In [ ]:
y = df['market_forward_excess_returns']
X = df.drop(['market_forward_excess_returns', 'risk_free_rate', 'forward_returns'], axis=1).astype('float64')

print(y.head())
print(X.head())

Lags = [1, 2, 5, 10, 21, 30]
Rolls = [5, 21, 63, 126, 252]

warmup_period = max(Lags + Rolls)

y_means = pd.DataFrame()
for roll in Rolls:
    y_means[f'y_mean{roll}'] = y.rolling(window=roll).mean()

y_std = pd.DataFrame()
for roll in Rolls:
    y_std[f'y_std{roll}'] = y.rolling(window=roll).std()

y_ewmstd = pd.DataFrame()
for roll in Rolls:
    y_ewmstd[f'y_ewmstd{roll}'] = y.ewm(span=roll, adjust=False, min_periods=roll).std() * np.sqrt(252)

y_min = pd.DataFrame()
for roll in Rolls:
    y_min[f'y_min{roll}'] = y.rolling(window=roll).min()
    
y_max = pd.DataFrame()
for roll in Rolls:
    y_max[f'y_max{roll}'] = y.rolling(window=roll).max()



y_lags = pd.DataFrame()

for lag in Lags:
    y_lags[f'y_lag{lag}'] = y.shift(lag)

X_lags = pd.DataFrame()

for lag in Lags:
    for cols in X.columns:
        X_lags[f'{cols}_lag{lag}'] = X[cols].shift(lag)

X_means = pd.DataFrame()

for roll in Rolls:
    for cols in X.columns:
        X_means[f'{cols}_mean{roll}'] = X[cols].rolling(window=roll).mean()

X_std = pd.DataFrame()

for roll in Rolls:
    for cols in X.columns:
        X_std[f'{cols}_std{roll}'] = X[cols].rolling(window=roll).std()
        
X_min = pd.DataFrame()

for roll in Rolls:
    for cols in X.columns:
        X_min[f'{cols}_min{roll}'] = X[cols].rolling(window=roll).min()
        
X_max = pd.DataFrame()

for roll in Rolls:
    for cols in X.columns:
        X_max[f'{cols}_max{roll}'] = X[cols].rolling(window=roll).max()

"""

For every var in X:

1. calculate relative change ( X_lag1 - X_1 ) / X_lag1

2. Add Median Skew Kurtosis to rolling moments, as well as rolling z-score

3. Volatility / signal proxies (mean of absolute deviate)
absΔX_W_mean = mean_W(|ΔX_1|)
varΔX_W = var_W(ΔX_1)
EWMA of |ΔX|

4. Regime-normalised 
X / EWMA(|ΔX|)

5. Saturation & non-linear transforms
log1p(|X|) * sign(X)
sqrt(|X|) * sign(X)
X^2
X^3

For y:

1. Momentum and trend
cumulative return over W: mom_W = Π(1 + r) - 1
price above / below trend: price / SMA_W(price) - 1

2. Volatility
vol_W = sqrt(252) * std_W(r); EWMA vol (λ ≈ 0.94)
Realized vol proxies: mean_W(|r|), mean_W(r^2)

3. Skew / Kurt of returns
skew_W(r) & kurt_W(r)

4. Drawdown metrics
Rolling max price; drawdown depth; max drawdown over W

5. Regime indicators (binary & ordinal)
High-vol regime: vol_W > quantile(vol_W, 0.7) for W in {21, 63}
Trend regime: mean_W(r) > 0 bull vs <= bear
Turbulance index (Mahalanobis distance of recent returns vs long-run mean/cov) if feasible

For X (Cross-feature interactions: pairwise within X):
1. Products & Ratios X1*X2, X1/(|X2|+ε))
2. Conditional Interactions X * 1[vol_regime=high], X * 1[trend_regime=bull]
3. Nonlinear mixes X^2 * Y, sign(X)*sqrt(|X|) * Y
4. Group Aggregates cross-sectional means, median std at each t, top-N trimmed mean.




"""

frames = [X_lags, y_lags, y_means, y_std, y_min, y_max, X_means, X_std, X_min, X_max]
X_full = X.join(frames)

X_model = X_full[warmup_period:].copy()
y_model = y[warmup_period:].copy()

0   -0.003038
1   -0.009114
2   -0.010243
3    0.004046
4   -0.012301
Name: market_forward_excess_returns, dtype: float64
   date_id   D1   D2   D3   D4   D5   D6   D7   D8   D9      E1     E10     E11     E12     E13     E14     E15     E16     E17     E18     E19      E2  \
0      0.0  0.0  0.0  0.0  1.0  1.0  0.0  0.0  0.0  1.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0   
1      1.0  0.0  0.0  0.0  1.0  1.0  0.0  0.0  0.0  1.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0   
2      2.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  1.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0   
3      3.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0   
4      4.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0 -9999.0

C:\Users\lhkke\AppData\Local\Temp\ipykernel_29308\584529104.py:37: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  X_lags[f'{cols}_lag{lag}'] = X[cols].shift(lag)
C:\Users\lhkke\AppData\Local\Temp\ipykernel_29308\584529104.py:37: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  X_lags[f'{cols}_lag{lag}'] = X[cols].shift(lag)
C:\Users\lhkke\AppData\Local\Temp\ipykernel_29308\584529104.py:37: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.

In [36]:
def evaluate_univariate_features(
    X: pd.DataFrame,
    y: pd.Series,
    n_splits: int = 5,
    test_size: int = 63, # ~3 months of trading days
    min_obs: int = 30, # minimum overlapping non-NaN obs required per fold
    features: list[str] | None = None,
    verbose: bool = True
) -> pd.DataFrame:
    
    """
    Evaluate univariate features using time series cross-validation.

    Parameters:
    - X: pd.DataFrame
        Feature set.
    - y: pd.Series
        Target variable.
    - n_splits: int
        Number of splits for TimeSeriesSplit.
    - test_size: int
        Size of the test set for each split.
        
    Returns a DataFrame with per-feature aggregated metrics:
        - coverage: non-NaN ratio
        - r2_train_mean/median/std, r2_test_mean/median/std
        - mse_train_mean/median/std, mse_test_mean/median/std
        - pearson_test_mean, spearman_test_mean
        - folds_used, frac_folds_r2_pos (share of folds with R^2_test > 0)
        
    """
    assert len(X) == len(y)
    
    X = X.copy()
    y = y.astype(float).copy()
    
    if features is None:
        features = list(X.columns)
        
    # pairwise coverage per feature (full sample)
    coverage = {f: float((X[f].notna() & y.notna()).mean()) for f in features}
    
    tscv = TimeSeriesSplit(n_splits=n_splits, test_size=test_size)
    
    results = []
    
    
    for f in features:
        r2_tr, r2_te, mse_tr, mse_te = [],[],[],[]
        pear_te, spear_te = [], []
        mse_improve_te = []
        folds_used = 0
        
        
        for fold_id, (tr_idx, te_idx) in enumerate(tscv.split(X), 1):
            x_tr = X[f].iloc[tr_idx]
            y_tr = y.iloc[tr_idx]
            x_te = X[f].iloc[te_idx]
            y_te = y.iloc[te_idx]
            
            m_tr = x_tr.notna() & y_tr.notna()
            m_te = x_te.notna() & y_te.notna()
            if m_tr.sum() < min_obs or m_te.sum() < min_obs:
                continue
            
            
            xtr = x_tr[m_tr].to_numpy().reshape(-1, 1)
            ytr = y_tr[m_tr].to_numpy().reshape(-1)
            xte = x_te[m_te].to_numpy().reshape(-1, 1)
            yte = y_te[m_te].to_numpy().reshape(-1)
            
            baseline_pred_test = np.full_like(yte, fill_value=ytr.mean(), dtype=float)
            baseline_mse_test = mean_squared_error(yte, baseline_pred_test)
            
            lr = LinearRegression()
            lr.fit(xtr, ytr)
            
            yhat_tr = lr.predict(xtr)
            yhat_te = lr.predict(xte)
            
            r2_tr.append(r2_score(ytr, yhat_tr))
            r2_te.append(r2_score(yte, yhat_te))
            mse_tr.append(mean_squared_error(ytr, yhat_tr))
            mse_te.append(mean_squared_error(yte, yhat_te))
            
            mse_improve_te.append(baseline_mse_test - mse_te[-1])
            
            pear_te.append(pd.Series(yte).corr(pd.Series(yhat_te), method='pearson'))
            spear_te.append(pd.Series(yte).corr(pd.Series(yhat_te), method='spearman'))
            
            
            folds_used += 1
            
        if folds_used == 0:
            if verbose:
                print(f"[skip] {f}: insufficient overlapping data across folds")
            continue
        
        def agg(v):
            return np.mean(v), np.median(v), np.std(v, ddof=1) if len(v) > 1 else 0.0
        
        
        r2_tr_mean, r2_tr_med, r2_tr_std = agg(r2_tr)
        r2_te_mean, r2_te_med, r2_te_std = agg(r2_te)
        mse_tr_mean, mse_tr_med, mse_tr_std = agg(mse_tr)
        mse_te_mean, mse_te_med, mse_te_std = agg(mse_te)
        
        
        results.append({
            "feature": f,
            "coverage": coverage[f],
            "folds_used": folds_used,
            "frac_folds_r2_pos": np.mean([x > 0 for x in r2_te]),
            
            "r2_train_mean": r2_tr_mean,
            "r2_train_medium": r2_tr_med,
            "r2_train_std": r2_tr_std,
            
            "r2_test_mean": r2_te_mean,
            "r2_test_medium": r2_te_med,
            "r2_te_std": r2_te_std,
            
            "mse_train_mean": mse_tr_mean,
            "mse_train_median": mse_tr_med,
            "mse_train_std": mse_tr_std,
            
            "mse_test_mean": mse_te_mean,
            "mse_test_median": mse_te_med,
            "mse_test_std": mse_te_std,
            
            
            "mse_improve_vs_baseline_mean": float(np.mean(mse_improve_te)),
            
            "pearson_test_mean": float(np.nanmean(pear_te)),
            "spearman_test_mean": float(np.nanmean(spear_te))

        })
        
        
    out = pd.DataFrame(results).sort_values(["r2_test_mean", "mse_improve_vs_baseline_mean"], ascending=[False, False])
    return out.reset_index(drop=True)
            
            

In [37]:
metrics_df = evaluate_univariate_features(
    X=X_model,
    y=y_model,
    n_splits=5,
    test_size=63,
    min_obs=30,
    features=None
)

print(metrics_df.head(20))

winners = metrics_df.query("coverage >= 0.8 and frac_folds_r2_pos >= 0.2 and r2_test_mean > 0")
winners.sort_values("mse_improve_vs_baseline_mean", ascending=False).head(20)

print(winners)

c:\Users\lhkke\Documents\HullTactical\HullTactical\lib\site-packages\pandas\core\nanops.py:1632: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  return spearmanr(a, b)[0]
c:\Users\lhkke\Documents\HullTactical\HullTactical\lib\site-packages\pandas\core\nanops.py:1632: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  return spearmanr(a, b)[0]
c:\Users\lhkke\Documents\HullTactical\HullTactical\lib\site-packages\pandas\core\nanops.py:1632: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  return spearmanr(a, b)[0]
c:\Users\lhkke\Documents\HullTactical\HullTactical\lib\site-packages\pandas\core\nanops.py:1632: ConstantInputWarning: An input array is constant; the correlation coefficient is not defined.
  return spearmanr(a, b)[0]
c:\Users\lhkke\Documents\HullTactical\HullTactical\lib\site-packages\pandas\core\nanops.py:1632: ConstantInputWarning: An in

                 feature  coverage  folds_used  frac_folds_r2_pos  r2_train_mean  r2_train_medium  r2_train_std  r2_test_mean  r2_test_medium  r2_te_std  \
0                y_mean5       1.0           5                1.0       0.185644         0.185720      0.000253      0.172681        0.154106   0.047739   
1                 y_max5       1.0           5                1.0       0.053583         0.053458      0.000294      0.053854        0.050931   0.021673   
2               y_mean21       1.0           5                0.8       0.046780         0.046683      0.000229      0.042548        0.055473   0.036033   
3                 y_min5       1.0           5                0.8       0.035565         0.035633      0.000200      0.028565        0.035613   0.052678   
4               y_mean63       1.0           5                0.6       0.015059         0.015044      0.000132     -0.004549        0.000194   0.014437   
5                y_max21       1.0           5                0.

In [38]:
metrics_df.to_csv('univariate_regression_metrics.csv')

PermissionError: [Errno 13] Permission denied: 'univariate_regression_metrics.csv'

In [ ]:
# _feature_re = re.compile(
#     r"""
#     ^(?P<family>y|date_id|[A-Z])           # family prefix: y, date_id, or single capital (M/V/E/...)
#     (?P<fid>\d+)?                          # optional numeric id like 10 in M10
#     (?:                                    # optional suffixes
#         _(?P<is_missing>is_missing)        # is_missing flag (may be followed by ops)
#         (?:_(?P<miss_op>lag|mean|min|max|std)
#            (?P<miss_win>\d+))?             # optional op+window after is_missing
#         |
#         _(?P<op>lag|mean|min|max|std)      # normal op (lag/mean/min/max/std)
#         (?P<win>\d+)?                      # optional window size after op
#     )?$
#     """,
#     re.VERBOSE
# )

# def parse_feature(name:str) -> dict:
#     m = _feature_re.match(name)
#     if not m:
#         return {
#             "family": "other",
#             "fid": np.nan,
#             "is_missing": False,
#             "op": "raw",
#             "window": np.nan,
#             "lag": np.nan,
#             "raw_name": name
#         }
#     gd = m.groupdict()
#     family = gd["family"]
#     fid = int(gd["fid"]) if gd["fid"] is not None else np.nan,
    
#     is_missing = gd["is_missing"] == "is_missing"
#     if is_missing:
#         op = gd["miss_op"] if gd["miss_op"] else "missing_flag"
#         window = int(gd["miss_win"]) if gd["miss_win"] else np.nan
#     else:
#         op = gd["op"] if gd["op"] else "raw"
#         window = int(gd["win"]) if gd["win"] else np.nan

#     # Independent lag capture if not already parsed
#     lag_m = re.search(r"lag(\d+)", name)
#     lag = int(lag_m.group(1)) if lag_m else (window if op == "lag" and not np.isnan(window) else np.nan)

#     return {
#         "family": family,                  # e.g. 'M', 'V', 'E', 'S', 'D', 'P', 'I', 'y', 'date_id'
#         "fid": fid,                        # numeric id if present (e.g. 10 for M10)
#         "is_missing": bool(is_missing),    # True if contains 'is_missing'
#         "op": op,                          # 'raw' | 'lag' | 'mean' | 'min' | 'max' | 'std' | 'missing_flag'
#         "window": window,                  # 5/21/63/126/252 if present
#         "lag": lag,                        # 1/2/5/10/21/30 if present
#         "raw_name": name
#     }
# print(metrics_df["feature"].head(5))
# parsed = pd.DataFrame([parse_feature(str(f)) for f in metrics_df["feature"]])

# parsed.to_csv('univariate_regression_metrics.csv')

# metrics_enriched = pd.concat([metrics_df, parsed], axis=1)

# def window_bucket(w):
#     if pd.isna(w): return "None"
#     w = int(w)
#     if w in (5, 10): return "short (≤10)"
#     if w in (21, 30): return "monthly (~21-30)"
#     if w == 63: return "quarter (~63)"
#     if w == 126: return "half-year (~126)"
#     if w == 252: return "year (~252)"
#     return f"window_{w}"
# metrics_enriched["window_bucket"] = metrics_enriched["window"].map(window_bucket)

# metrics_enriched["kind"] = np.where(metrics_enriched["is_missing"], "missing-derived", "value-derived")


0     y_mean5
1      y_max5
2    y_mean21
3      y_min5
4    y_mean63
Name: feature, dtype: object


In [39]:
MIN_INVESTMENT = 0.0
MAX_INVESTMENT = 2.0
TRADING_DAYS_PER_YR = 252

class ParticipantVisibleError(Exception):
    pass

def adjusted_sharpe_from_df(solution: pd.DataFrame, submission: pd.DataFrame, row_id_col: str) -> float:
    """
    solution: columns = [row_id_col, 'forward_returns', 'risk_free_rate']
    submission: columns = [row_id_col, 'prediction'] where prediction ∈ [0,2]
    """
    if not pd.api.types.is_numeric_dtype(submission['prediction']):
        raise ParticipantVisibleError('Predictions must be numeric')
    sol = solution.copy()
    sub = submission.copy()

    # align on row_id
    sol = sol.merge(sub[[row_id_col, 'prediction']], on=row_id_col, how='inner')
    sol.rename(columns={'prediction': 'position'}, inplace=True)

    if sol['position'].max() > MAX_INVESTMENT:
        raise ParticipantVisibleError(f'Position of {sol["position"].max()} exceeds maximum of {MAX_INVESTMENT}')
    if sol['position'].min() < MIN_INVESTMENT:
        raise ParticipantVisibleError(f'Position of {sol["position"].min()} below minimum of {MIN_INVESTMENT}')

    # Strategy daily returns: convex combo of RF and market forward return
    sol['strategy_returns'] = sol['risk_free_rate'] * (1 - sol['position']) + sol['position'] * sol['forward_returns']

    # Strategy Sharpe (excess mean / std) annualized
    strategy_excess = sol['strategy_returns'] - sol['risk_free_rate']
    # geometric to arithmetic mean per-day
    cum = (1 + strategy_excess).prod()
    mean_excess_daily = cum ** (1 / len(sol)) - 1
    std_daily = sol['strategy_returns'].std()
    if std_daily == 0:
        raise ParticipantVisibleError('Division by zero, strategy std is zero')

    sharpe = mean_excess_daily / std_daily * np.sqrt(TRADING_DAYS_PER_YR)
    strategy_vol_annual = float(std_daily * np.sqrt(TRADING_DAYS_PER_YR) * 100)

    # Market stats (forward_returns vs risk_free_rate)
    market_excess = sol['forward_returns'] - sol['risk_free_rate']
    market_cum = (1 + market_excess).prod()
    market_mean_excess_daily = market_cum ** (1 / len(sol)) - 1
    market_std_daily = sol['forward_returns'].std()
    if market_std_daily == 0:
        raise ParticipantVisibleError('Division by zero, market std is zero')
    market_vol_annual = float(market_std_daily * np.sqrt(TRADING_DAYS_PER_YR) * 100)

    # Penalties (vol & return gap)
    excess_vol = max(0, strategy_vol_annual / market_vol_annual - 1.2) if market_vol_annual > 0 else 0
    vol_penalty = 1 + excess_vol

    return_gap = max(0, (market_mean_excess_daily - mean_excess_daily) * 100 * TRADING_DAYS_PER_YR)
    return_penalty = 1 + (return_gap ** 2) / 100

    adjusted = sharpe / (vol_penalty * return_penalty)
    return float(min(adjusted, 1_000_000.0))


In [40]:
def signal_to_position(train_pred: np.ndarray, test_pred: np.ndarray, beta: float = 0.25):
    """
    Standardize predictions on TRAIN, map to positions: pos = 1 + beta * z
    Then clip to [0, 2].
    beta controls aggressiveness; increase to take more risk.
    """
    mu, sigma = np.mean(train_pred), np.std(train_pred)
    if sigma == 0:
        # fallback: constant signal → neutral position
        return np.full_like(test_pred, 1.0, dtype=float)

    z = (test_pred - mu) / sigma
    pos = 1.0 + beta * z
    return np.clip(pos, MIN_INVESTMENT, MAX_INVESTMENT)

In [41]:
N_SAMPLES = len(df)
N_SPLITS = 5
TEST_SIZE = 252

tscv = TimeSeriesSplit(
    n_splits=N_SPLITS,
    test_size=TEST_SIZE
)

lgbm_model = LGBMRegressor(
    objective='regression',
    n_estimators=100,
    learning_rate=0.1,
    random_state=42,
    verbose=-1
)

lgbmr2_scores = []
lgbmmse_scores = []

print(f"Starting Walk-Forward Validation with {N_SPLITS} folds (Test size: {TEST_SIZE} days)")
print("-" * 50)

for fold, (train_index, test_index) in enumerate(tscv.split(X_model)):
    X_train, X_test = X.iloc[train_index], X.iloc[test_index]
    y_train, y_test = y.iloc[train_index], y.iloc[test_index]

    lgbm_model.fit(X_train, y_train)

    y_pred = lgbm_model.predict(X_test)
    fold_r2 = r2_score(y_test, y_pred)
    fold_mse = mean_squared_error(y_test, y_pred)

    lgbmr2_scores.append(fold_r2)
    lgbmmse_scores.append(fold_mse)

    print(f"Fold {fold + 1}:")
    print(f"  Train Size: {len(X_train):,}")
    print(f"  Test Size:  {len(X_test):,}")
    print(f"  R-squared:  {fold_r2:.6f}")
    print(f"  MSE:        {fold_mse:.6f}")
    print("-" * 50)

print("\n--- Final Walk-Forward Results ---")
print(f"Average R-squared: {np.mean(lgbmr2_scores):.6f} ± {np.std(lgbmr2_scores):.6f}")
print(f"Average MSE:       {np.mean(lgbmmse_scores):.6f} ± {np.std(lgbmmse_scores):.6f}")

Starting Walk-Forward Validation with 5 folds (Test size: 252 days)
--------------------------------------------------
Fold 1:
  Train Size: 7,478
  Test Size:  252
  R-squared:  -0.167182
  MSE:        0.000263
--------------------------------------------------
Fold 2:
  Train Size: 7,730
  Test Size:  252
  R-squared:  -0.181465
  MSE:        0.000095
--------------------------------------------------
Fold 3:
  Train Size: 7,982
  Test Size:  252
  R-squared:  -0.067313
  MSE:        0.000189
--------------------------------------------------
Fold 4:
  Train Size: 8,234
  Test Size:  252
  R-squared:  -0.157762
  MSE:        0.000141
--------------------------------------------------
Fold 5:
  Train Size: 8,486
  Test Size:  252
  R-squared:  -0.026221
  MSE:        0.000065
--------------------------------------------------

--- Final Walk-Forward Results ---
Average R-squared: -0.119988 ± 0.061645
Average MSE:       0.000151 ± 0.000070


In [45]:
N_SAMPLES = len(df)
N_SPLITS = 5
TEST_SIZE = 252
GAP = 252

ROW_ID_COL = "row_id"
df_eval = df.copy()
df_eval[ROW_ID_COL] = df_eval.index



tscv = TimeSeriesSplit(
    n_splits=N_SPLITS,
    test_size=TEST_SIZE,
    gap=GAP
)

xgb_model = XGBRegressor(
    objective='reg:squarederror',
    learning_rate=0.01,
    n_estimators=5000,          # upper bound; early stopping will cut it
    max_depth=4,                # 3–6 is a sensible range
    min_child_weight=5,         # 1–20; raises leaf sample requirement
    subsample=0.8,
    colsample_bytree=0.8,
    reg_lambda=2.0,             # L2 regularization helps stability
    reg_alpha=0.0,
    random_state=42,
    n_jobs=-1,
    tree_method='hist',
    eval_metric='rmse',
    max_bin=256                 # optional; keeps splits stable
)

xgb_scores = []
xgbmse_scores = []

r2s, mses, adj_sharpes = [], [], []

print(f"Starting Walk-Forward Validation with {N_SPLITS} folds (Test size: {TEST_SIZE} days)")
print("-" * 60)

for fold, (train_index, test_index) in enumerate(tscv.split(X_model)):
    X_tr, X_te = X.iloc[train_index], X.iloc[test_index]
    y_tr, y_te = y.iloc[train_index], y.iloc[test_index]

    xgb_model.fit(
        X_tr, y_tr,
        eval_set=[(X_tr, y_tr), (X_te, y_te)],
        verbose=False,
    )

    y_hat_tr = xgb_model.predict(X_tr)
    y_hat_te = xgb_model.predict(X_te)

    # Standard metrics
    r2 = r2_score(y_te, y_hat_te)
    mse = mean_squared_error(y_te, y_hat_te)
    r2s.append(r2); mses.append(mse)

    # === Map raw predictions to positions in [0,2] (choose one mapping) ===
    pos_te = signal_to_position(y_hat_tr, y_hat_te, beta=0.25)
    # pos_te = signal_to_position_percentile(y_hat_tr, y_hat_te, lo=5, hi=95)

    # Build solution/submission frames for THIS fold
    sol_fold = df_eval.loc[X_te.index, [ROW_ID_COL, "forward_returns", "risk_free_rate"]].copy()
    sub_fold = pd.DataFrame({ROW_ID_COL: df_eval.loc[X_te.index, ROW_ID_COL].values,
                             "prediction": pos_te.astype(float)})

    # Competition metric
    adj = adjusted_sharpe_from_df(sol_fold, sub_fold, row_id_col=ROW_ID_COL)
    adj_sharpes.append(adj)

    print(f"Fold {fold}: train={len(X_tr):,} test={len(X_te):,} | "
          f"best_iter={getattr(xgb_model, 'best_iteration', None)}  "
          f"R²={r2:.6f}  MSE={mse:.6f}  AdjSharpe={adj:.6f}")

print("\n--- Summary ---")
print(f"R²:          mean={np.mean(r2s):.6f}  std={np.std(r2s):.6f}")
print(f"MSE:         mean={np.mean(mses):.6f}  std={np.std(mses):.6f}")
print(f"AdjSharpe:   mean={np.mean(adj_sharpes):.6f}  std={np.std(adj_sharpes):.6f}  "
      f"max={np.max(adj_sharpes):.6f}")

Starting Walk-Forward Validation with 5 folds (Test size: 252 days)
------------------------------------------------------------
Fold 0: train=7,226 test=252 | best_iter=None  R²=-0.694071  MSE=0.000382  AdjSharpe=0.446247
Fold 1: train=7,478 test=252 | best_iter=None  R²=-1.112938  MSE=0.000171  AdjSharpe=1.470305
Fold 2: train=7,730 test=252 | best_iter=None  R²=-0.152386  MSE=0.000204  AdjSharpe=-0.209883
Fold 3: train=7,982 test=252 | best_iter=None  R²=-0.101754  MSE=0.000134  AdjSharpe=0.438911
Fold 4: train=8,234 test=252 | best_iter=None  R²=-0.341998  MSE=0.000085  AdjSharpe=1.256106

--- Summary ---
R²:          mean=-0.480630  std=0.378386
MSE:         mean=0.000195  std=0.000101
AdjSharpe:   mean=0.680337  std=0.610104  max=1.470305
